# Drillhole creation and quick visualiation

In [ ]:
import geolime as geo
from pyproj import CRS
import pyvista as pv

pv.set_jupyter_backend('html')
geo.Project().set_crs(CRS("EPSG:20350"))

# Loading DrillHoles

In [ ]:
dh = geo.read_file("../data/dh_hyper.geo")

In [ ]:
dh.user_properties()

The basic properties of a drillholes object already have unit specify

In [ ]:
dh.property("X_M").unit

Unit can also be specified in the Project for each property. 

Property units are managed using the Pint python pacakge (https://pint.readthedocs.io/en/stable/index.html). Default unit are already available (https://github.com/hgrecco/pint/blob/master/pint/default_en.txt) and other can be added to a GeoLime project

This will allow to specify the percent property to each property of a GeoLime object.

In [ ]:
geo.Project().unit_registry.define("percent = 1e-2 frac = pct")

Using the percent unit defined, we can now specify it to all other related property, especially the ones with `_pct` in their names.

In [ ]:
for prop in dh.properties():
    if "_pct" in dh.property(prop).name:
        dh.property(prop).unit = geo.Project().unit_registry.pct

In [ ]:
dh.property("Fe_pct").unit

## Graphic representations 

In [ ]:
geo.scatter(geo_object=dh, property_x="X_M", property_y="Z_M")

In [ ]:
geo.scatter(geo_object=dh, property_x="Y_M", property_y="Z_M")

Points with no value can be hidden using extra keywords from the folium library: https://python-visualization.github.io/folium/quickstart.html#Getting-Started 

In [ ]:
dh.plot_2d(property="Fe_pct", agg_method="mean", interactive_map=True, style_kwds={"fillColor": "none"})

In [ ]:
geo.scatter(geo_object=dh, property_x="Fe_pct", property_y="Z_M", marginal_plot="Histogram")

# Exploratory Analysis

In [ ]:
df_pv = dh.to_pyvista('Fe_pct')

In [ ]:
pl = pv.Plotter()
pl.add_mesh(df_pv.tube(radius=10))
pl.set_scale(zscale=20)

pl.show()

## Geological section

In [ ]:
geo.scatter(
    geo_object=dh, 
    property_x="Fe_pct", 
    property_y="Z_M", 
    region="(Y_M > 7475791.8 - 400) &  (Y_M < 7475791.8 + 400)"
)

Scatter function takes also into account all layout properties from plotly : https://plotly.com/python/reference/layout/.

As GeoLime plotting functions returns Plotly Figure, they can be stored in a variable.

In [ ]:
f = geo.scatter(
    geo_object=dh, 
    property_x="X_M", 
    property_y="FROM", 
    region="(Y_M > 7475791.8 - 20) &  (Y_M < 7475791.8 + 20)", 
    yaxis_autorange="reversed"
)

Plotly figures can then be exported to

- standard image format (PNG, PDF, JPEG) for static export
- HTML format for interactive export and sharing only figure without code
- JSON format to be used in other software or in a Web Application
- python dictionnary to understand figure architecture and modify every elements

In [ ]:
f.to_dict()

For example, we can change the color by setting a property from the drillholes, here we color the point using the Iron content

In [ ]:
f["data"][0]["marker"]["color"] = dh.data("Fe_pct", "(Y_M > 7475791.8 - 20) &  (Y_M < 7475791.8 + 20)")
f["data"][0]["marker"]["line"]["width"] = 0

In [ ]:
f

In [ ]:
f["data"][0]["marker"]["colorscale"] = "cividis"

In [ ]:
f

## Correlations between elements

In [ ]:
geo.correlation_heatmap(
    geo_object=dh, 
    properties=[
        "Mn_pct", "P_pct", "Fe_pct", "CaO_pct", "MgO_pct", "S_pct", "Al2O3", "TiO2_pct", "SiO2_pct", "K2O_pct"
    ]
)

In [ ]:
geo.scatter(geo_object=dh, property_x="Al2O3", property_y="Fe_pct", marginal_plot=geo.ScatterMethod.HISTOGRAM)

## Histograms

### Iron

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "FROM <= 10"},
        {"object": dh, "property": "Fe_pct", "region": "FROM > 10"}
    ],
    nbins=30
)

### Aluminium

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Al2O3"}], nbins=30)

### Titanium

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "TiO2_pct"}], nbins=30)

## Conclusions

As we can see with the visualization above, the main element in this area is Iron, mainly as an oxyde (Hematite/Goethite). Secondly, the geological sections  and various scatter showed us that the iron is located in two separate deposits, the first one being located near 10 meters deep, and the other around 50m.
This distribution of iron seems to show again in the histograms by its bimodal adspect.

Our tools have also revealed the presence of Al2O3 and TiO2, which are highly correlated (0.7 according to our heatmap, and located in the same areas, indicating a common backgroud and deposit history. However, their distribution is way lower than the iron one (Maximum 60% for the iron against 30% for the Aluminium and 3% Titanium), and they exist as punctual traces, not well defined deposits.